In [ ]:
%matplotlib inline


# GP regression

We want to approximate a discipline with two inputs and two outputs:

- $y_1=1+2x_1+3x_2$
- $y_2=-1-2x_1-3x_2$

over the unit hypercube $[0,1]\times[0,1]$.


In [ ]:
from __future__ import absolute_import, division, print_function, unicode_literals

from future import standard_library
from numpy import array

from gemseo.api import (
    configure_logger,
    create_design_space,
    create_discipline,
    create_scenario,
)
from gemseo.mlearning.api import create_regression_model

configure_logger()

standard_library.install_aliases()

## Create the discipline to learn
We can implement this analytic discipline by means of the
:class:`~gemseo.core.analytic_discipline.AnalyticDiscipline` class.



In [ ]:
expressions_dict = {"y_1": "1+2*x_1+3*x_2", "y_2": "-1-2*x_1-3*x_2"}
discipline = create_discipline(
    "AnalyticDiscipline", name="func", expressions_dict=expressions_dict
)

## Create the input sampling space
We create the input sampling space by adding the variables one by one.



In [ ]:
design_space = create_design_space()
design_space.add_variable("x_1", l_b=0.0, u_b=1.0)
design_space.add_variable("x_2", l_b=0.0, u_b=1.0)

## Create the learning set
We can build a learning set by means of a
:class:`~gemseo.core.doe_scenario.DOEScenario` with a full factorial design of
experiments. The number of samples can be equal to 9 for example.



In [ ]:
discipline.set_cache_policy(discipline.MEMORY_FULL_CACHE)
scenario = create_scenario(
    [discipline], "DisciplinaryOpt", "y_1", design_space, scenario_type="DOE"
)
scenario.execute({"algo": "fullfact", "n_samples": 9})

## Create the regression model
Then, we build the linear regression model from the discipline cache and
displays this model.



In [ ]:
dataset = discipline.cache.export_to_dataset()
model = create_regression_model("GaussianProcessRegression", data=dataset)
model.learn()
print(model)

## Predict output
Once it is built, we can use it for prediction.



In [ ]:
input_value = {"x_1": array([1.0]), "x_2": array([2.0])}
output_value = model.predict(input_value)
print(output_value)